## Battle of the Neighborhoods using Segmenting and Clustering for Rome Italy.

### I have chosen three countries to do a comparison of the different towns / neighborhoods Rome Italy is the second one.
## Introduction

In the battle of the neighborhoods I will be comparing three different countries towns / neighborhoods using Foursquare API. The purpose of using the Foursquare API is to explore neighborhoods in Rome Italy. The **explore** function will get the most common venue categories in each town / neighborhood, and then use this feature to group the neighborhoods into clusters. I will use the *k*-means clustering algorithm to complete this task. Finally, I will use the Folium library to visualize the neighborhoods in Lazio, Italy and their emerging clusters.

#### Call in the neccessary pandas modules.

In [36]:
import numpy as np # library to handle data in a vectorized manner

import csv # Handles csv files

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

# uncomment this line if you haven't completed the Foursquare API lab
#!conda install -c conda-forge geopy --yes 
import geopy.geocoders 

# convert an address into latitude and longitude values
from geopy.geocoders import Nominatim 
from geopy.geocoders import GoogleV3

import requests # library to handle requests

# tranform JSON file into a pandas dataframe
from pandas.io.json import json_normalize 

#Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors


#import k-means from clustering stage
from sklearn.cluster import KMeans

# uncomment this line if you haven't completed the Foursquare API lab
#!conda install -c conda-forge folium=0.5.0 --yes 
import folium # map rendering library

#Installing Beautiful Soup
from bs4 import BeautifulSoup

print('Libraries imported.')

Libraries imported.


#### Read in CSV file containing Italy coordinates.

In [37]:
Italy_data = pd.read_csv('it.csv')

#### Panadas Head to view first 5 rows of the dataframe.

In [38]:
Italy_data.head(5)

city        lat        lng country iso2     admin  capital  population  \
0      Rome  41.900000  12.483333   Italy   IT     Lazio  primary   3339000.0   
1     Milan  45.466667   9.200000   Italy   IT  Lombardy    admin   2945000.0   
2    Naples  40.833333  14.250000   Italy   IT  Campania    admin   2250000.0   
3     Turin  45.050000   7.666667   Italy   IT  Piedmont    admin   1652000.0   
4  Florence  43.766667  11.250000   Italy   IT   Tuscany    admin   1500000.0   

   population_proper  
0            35452.0  
1          1306661.0  
2           988972.0  
3           865263.0  
4           371517.0

#### Pandas Tail to view last five rows of dataframe.

In [39]:
Italy_data.tail(5)

city        lat        lng country iso2                  admin  \
113     Pesaro  43.900000  12.916667   Italy   IT                 Marche   
114  Pordenone  45.963889  12.657500   Italy   IT  Friuli-Venezia Giulia   
115       Lodi  45.316667   9.500000   Italy   IT               Lombardy   
116    Brescia  45.550000  10.250000   Italy   IT               Lombardy   
117  Agrigento  37.316667  13.566667   Italy   IT                Sicilia   

    capital  population  population_proper  
113   minor         NaN                NaN  
114   minor         NaN                NaN  
115   minor         NaN                NaN  
116   minor         NaN                NaN  
117   minor         NaN                NaN

#### We are going to use Pandas drop to remove  the following columns that are not necessary in the dataframe iso2, capital, population and population_proper. 

In [40]:
Italy_data.drop(['iso2', 'capital', 'population_proper'], axis = 1, inplace = True )
Italy_data.head(5)

city        lat        lng country     admin  population
0      Rome  41.900000  12.483333   Italy     Lazio   3339000.0
1     Milan  45.466667   9.200000   Italy  Lombardy   2945000.0
2    Naples  40.833333  14.250000   Italy  Campania   2250000.0
3     Turin  45.050000   7.666667   Italy  Piedmont   1652000.0
4  Florence  43.766667  11.250000   Italy   Tuscany   1500000.0

In [41]:
import pandas_bokeh
pandas_bokeh.output_notebook()

Loading BokehJS ...

In [42]:
Italy_data.plot_bokeh.map(
    x="lng",
    y="lat",
    hovertool_string="""<h2> @{city} </h2> 
                        <h3> @{country} </h3> 
                        <h3> @{admin} <h3>
                        <h3> Population : @{population}  </h3>""",
                        
    tile_provider="STAMEN_TERRAIN_RETINA",
    figsize=(1000, 800),
    title="Italy with its' cities")

Figure(id='1248', ...)

#### This is a list of the neighborhoods in Italy by region.

In [43]:
Italy_towns = pd.read_csv('Towns in Italy.csv')
Italy_towns.head()

Town Region Country   Latitude  Longitude
0             Rome  Lazio   Italy  41.894802  12.485338
1          Affile   Lazio   Italy  41.884122  13.032688
2          Agosta   Lazio   Italy  41.981624  13.032688
3  Albano Laziale   Lazio   Italy  41.728889  12.658269
4       Allumiere   Lazio   Italy  42.156218  11.903832

#### Pandas tail to view the last rows of dataframe.

In [44]:
Italy_towns.tail(5)

Town                 Region Country   Latitude  Longitude
202         Brembate                Bergamo   Italy  45.604397   9.559232
203     Nocera Umbra                Perugia   Italy  43.118526  12.787743
204  Gardone Riviera                Brescia   Italy  45.618183  10.559564
205           Sirolo                 Ancona   Italy  43.519100  13.621703
206          Sarzana  Province of La Spezia   Italy  44.112457   9.962840

#### Checking data type in the dataframe

In [45]:
Italy_towns.dtypes

Town          object
Region        object
Country       object
Latitude     float64
Longitude    float64
dtype: object

#### Use geopy library to get the latitude and longitude values of Rome City.

In [46]:
#In order to define an instance of the geocoder, we need to define a user_agent. We will name our agent tor_explorer, as shown below.
address = 'Rome, IT'

geolocator = Nominatim(user_agent="it_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Rome City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Rome City are 41.894802, 12.4853384.


#### Create a map of Rome Italy with its towns and regions superimposed on top.

In [80]:
# create map of Rome Italy using latitude and longitude values
map_rome = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, Town, Region in zip(Italy_towns['Latitude'], Italy_towns['Longitude'], Italy_towns['Town'], Italy_towns['Region']):
    label = '{}, {}'.format(Italy_towns, Town)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_rome)  
    
map_rome

**Folium** is a great visualization library.

However, for illustration purposes, let's simplify the above map and segment and cluster only the neighborhoods in the region of Lazio. So let's slice the original dataframe and create a new dataframe of the region of Lazio data.

In [48]:
lazio_data = Italy_towns[Italy_towns['Region'] == 'Lazio']
lazio_data.head()

Town Region Country   Latitude  Longitude
0             Rome  Lazio   Italy  41.894802  12.485338
1          Affile   Lazio   Italy  41.884122  13.032688
2          Agosta   Lazio   Italy  41.981624  13.032688
3  Albano Laziale   Lazio   Italy  41.728889  12.658269
4       Allumiere   Lazio   Italy  42.156218  11.903832

In [49]:
lazio_data.tail()

Town Region Country   Latitude  Longitude
118       Velletri   Lazio   Italy  41.686701  12.777043
119       Vicovaro   Lazio   Italy  42.017941  12.897230
120  Vivaro Romano   Lazio   Italy  42.099826  13.006686
121       Zagarolo   Lazio   Italy  41.838383  12.831050
129          Tivoli  Lazio   Italy  41.959721  12.798056

Let's get the geographical coordinates of Lazio Italy.

In [50]:
address = 'Lazio, IT'

geolocator = Nominatim(user_agent="it_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Lazio are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Lazio are 41.9808038, 12.7662312.


As we did with all of Rome, Italy, let's visualize Lazio with the neighborhoods in it.

In [51]:
# create map of Lazio using latitude and longitude values
map_lazio = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(lazio_data['Latitude'], lazio_data['Longitude'], lazio_data['Town']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_lazio)  
    
map_lazio

Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

Let's get the neighborhood name from our dataframe

#### Define Foursquare Credentials and Version

In [52]:
CLIENT_ID = 'VJJFJWFM01TSOX1MMDUPIJXKGYFI1XR2TJZ5A5JUKMX3XRHU' # your Foursquare ID
CLIENT_SECRET = 'D5NCPNBUTVJPTJD4QK2UE33V52TDMDXIWKHKZTLLQVCXJGLQ' # your Foursquare Secret
VERSION = '20180604' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: VJJFJWFM01TSOX1MMDUPIJXKGYFI1XR2TJZ5A5JUKMX3XRHU
CLIENT_SECRET:D5NCPNBUTVJPTJD4QK2UE33V52TDMDXIWKHKZTLLQVCXJGLQ


### Lets explore the first neighborhood in our dataframe. 

#### Get the name of the town in the dataframe.

In [53]:
lazio_data.loc[0, 'Town']

'Rome'

Get the neighborhood's latitude and longitude values.

In [54]:
town_latitude = lazio_data.loc[0, 'Latitude'] # neighborhood latitude value
town_longitude = lazio_data.loc[0, 'Longitude'] # neighborhood longitude value

town_name = lazio_data.loc[0, 'Town'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(town_name, 
                                                               town_latitude, 
                                                               town_longitude))

Latitude and longitude values of Rome are 41.894802, 12.4853384.


#### Now, let's get the top 100 venues that are in Marble Hill within a radius of 500 meters.

First, let's create the GET request URL. Name your URL **url**.

In [55]:
# type your answer here
LIMIT = 100
radius = 500
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET, VERSION, town_latitude, town_longitude, radius, LIMIT)


Send the GET request and examine the results

In [56]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5dfe1a5d618f43001b9c2493'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'},
    {'name': 'With specials', 'key': 'specials'}]},
  'headerLocation': 'Monti',
  'headerFullLocation': 'Monti, Rome',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 91,
  'suggestedBounds': {'ne': {'lat': 41.8993020045, 'lng': 12.49137248200435},
   'sw': {'lat': 41.890301995499996, 'lng': 12.47930431799565}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4c41fd5c520fa593517ccaac',
       'name': 'Foro di Traiano',
       'location': {'address': 'Piazza Foro Traiano',
        'lat': 41.89472893619501,
        'lng': 12.4848713109981,
        'labeledLatLngs': [{'label': '

We know that all the information is in the *items* key. Before we proceed, let's borrow the **get_category_type** function from  Foursquare.

In [57]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

Now we are ready to clean the json and structure it into a *pandas* dataframe.

In [58]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name           categories  \
0                                Foro di Traiano        Historic Site   
1                                 Foro di Cesare        Historic Site   
2            Zuil van Trajanus (Colonna Traiana)  Monument / Landmark   
3                       Terrazza delle Quadrighe       Scenic Lookout   
4  Mercati di Traiano - Museo dei Fori Imperiali       History Museum   

         lat        lng  
0  41.894729  12.484871  
1  41.894128  12.485232  
2  41.895816  12.484276  
3  41.894346  12.483336  
4  41.896288  12.485973

How many venues were return by Foursquare?

In [59]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

91 venues were returned by Foursquare.


## Explore Neighborhoods in Lazio

Let's create a function to repeat the process to all neighborhoods in Lazio, Italy.

In [60]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Town', 
                  'Town Latitude', 
                  'Town Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

#### Now write the code to run the above function on each neighborhood and create a new dataframe called *Lazio_venues*.

In [61]:
# Code to run on each neighborhood in Lazio, Italy.
lazio_venues = getNearbyVenues(names=lazio_data['Town'],
                                   latitudes=lazio_data['Latitude'],
                                   longitudes=lazio_data['Longitude']
                                  )

Rome
Affile 
Agosta 
Albano Laziale 
Allumiere 
Anguillara Sabazia 
Anticoli Corrado 
Anzio 
Arcinazzo Romano 
Ardea 
Ariccia 
Arsoli 
Artena 
Bellegra 
Bracciano 
Camerata Nuova 
Campagnano di Roma 
Canale Monterano 
Canterano 
Capena 
Capranica Prenestina 
Carpineto Romano 
Casape 
Castel Gandolfo 
Castel Madama 
Castel San Pietro Romano 
Castelnuovo di Porto 
Cave 
Cerreto Laziale 
Cervara di Roma 
Cerveteri 
Ciampino 
Ciciliano 
Cineto Romano 
Civitavecchia 
Civitella San Paolo 
Colleferro 
Colonna 
Fiano Romano 
Filacciano 
Fiumicino 
Fonte Nuova 
Formello 
Frascati 
Gallicano nel Lazio 
Gavignano 
Genazzano 
Genzano di Roma 
Gerano 
Gorga 
Grottaferrata 
Guidonia Montecelio 
Jenne 
Labico 
Ladispoli 
Lanuvio 
Lariano 
Licenza 
Magliano Romano 
Mandela 
Manziana 
Marano Equo 
Marcellina 
Marino 
Mazzano Romano 
Mentana 
Monte Compatri 
Monte Porzio Catone 
Monteflavio 
Montelanico 
Montelibretti 
Monterotondo 
Montorio Romano 
Moricone 
Morlupo 
Nazzano 
Nemi 
Nerola 
Nettuno 
Ole

## Lets check the size of the dataframe

In [62]:
print(lazio_venues.shape)
lazio_venues.head()

(713, 7)


Town  Town Latitude  Town Longitude  \
0  Rome      41.894802       12.485338   
1  Rome      41.894802       12.485338   
2  Rome      41.894802       12.485338   
3  Rome      41.894802       12.485338   
4  Rome      41.894802       12.485338   

                                           Venue  Venue Latitude  \
0                                Foro di Traiano       41.894729   
1                                 Foro di Cesare       41.894128   
2            Zuil van Trajanus (Colonna Traiana)       41.895816   
3                       Terrazza delle Quadrighe       41.894346   
4  Mercati di Traiano - Museo dei Fori Imperiali       41.896288   

   Venue Longitude       Venue Category  
0        12.484871        Historic Site  
1        12.485232        Historic Site  
2        12.484276  Monument / Landmark  
3        12.483336       Scenic Lookout  
4        12.485973       History Museum

Lets check how many venues were returned for each neighborhood

#### Let's find out how many unique categories can be curated from all the returned venues

In [63]:
lazio_venues.groupby('Town').count()

Town Latitude  Town Longitude  Venue  \
Town                                                              
Agosta                                 1               1      1   
Albano Laziale                         4               4      4   
Allumiere                              5               5      5   
Anguillara Sabazia                     4               4      4   
Anticoli Corrado                       4               4      4   
Anzio                                 24              24     24   
Arcinazzo Romano                       2               2      2   
Ardea                                  4               4      4   
Ariccia                               18              18     18   
Arsoli                                 2               2      2   
Artena                                 4               4      4   
Campagnano di Roma                     4               4      4   
Canale Monterano                       3               3      3   
Capena                                 3               3      3   
Capranica Prenestina                   2               2      2   
Carpineto Romano                       4               4      4   
Casape                                 1               1      1   
Castel Gandolfo                       12              12     12   
Castel Madama                          2               2      2   
Castel San Pietro Romano               2               2      2   
Castelnuovo di Porto                   2               2      2   
Cave                                   5               5      5   
Cerreto Laziale                        4               4      4   
Cervara di Roma                        4               4      4   
Cerveteri                              5               5      5   
Ciampino                               8               8      8   
Cineto Romano                          2               2      2   
Civitavecchia                         19              19     19   
Civitella San Paolo                    2               2      2   
Colleferro                             4               4      4   
Colonna                                5               5      5   
Fiano Romano                           3               3      3   
Filacciano                             1               1      1   
Fiumicino                              9               9      9   
Fonte Nuova                            7               7      7   
Formello                               4               4      4   
Frascati                              28              28     28   
Gallicano nel Lazio                    2               2      2   
Gavignano                              3               3      3   
Genazzano                              1               1      1   
Genzano di Roma                        6               6      6   
Gerano                                 1               1      1   
Gorga                                  1               1      1   
Grottaferrata                         18              18     18   
Jenne                                  2               2      2   
Labico                                 3               3      3   
Ladispoli                              4               4      4   
Lanuvio                                3               3      3   
Lariano                                4               4      4   
Licenza                                2               2      2   
Mandela                                2               2      2   
Manziana                               9               9      9   
Marano Equo                            1               1      1   
Marcellina                             4               4      4   
Marino                                 4               4      4   
Mazzano Romano                         2               2      2   
Mentana                                4               4      4   
Monte Compatri                         3               3      3   
Monte P

#### Let's find out how many unique categories can be curated from all the returned venues

In [64]:
print('There are {} uniques categories.'.format(len(lazio_venues['Venue Category'].unique())))

There are 132 uniques categories.


## Analyze Each Neighborhood

In [65]:
# one hot encoding
lazio_onehot = pd.get_dummies(lazio_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
lazio_onehot['Town'] = lazio_venues['Town'] 

# move neighborhood column to the first column
fixed_columns = [lazio_onehot.columns[-1]] + list(lazio_onehot.columns[:-1])
lazio_onehot = lazio_onehot[fixed_columns]

lazio_onehot.head()

Town  Accessories Store  Airport Service  Alternative Healer  Art Gallery  \
0  Rome                  0                0                   0            0   
1  Rome                  0                0                   0            0   
2  Rome                  0                0                   0            0   
3  Rome                  0                0                   0            0   
4  Rome                  0                0                   0            0   

   Art Museum  Arts & Entertainment  BBQ Joint  Bakery  Bar  Bed & Breakfast  \
0           0                     0          0       0    0                0   
1           0                     0          0       0    0                0   
2           0                     0          0       0    0                0   
3           0                     0          0       0    0                0   
4           0                     0          0       0    0                0   

   Bistro  Bookstore  Brazilian Restaurant  Breakfast Spot  Brewery  \
0       0          0                     0               0        0   
1       0          0                     0               0        0   
2       0          0                     0               0        0   
3       0          0                     0               0        0   
4       0          0                     0               0        0   

   Bridal Shop  Burger Joint  Bus Station  Business Service  Cafeteria  Café  \
0            0             0            0                 0          0     0   
1            0             0            0                 0          0     0   
2            0             0            0                 0          0     0   
3            0             0            0                 0          0     0   
4            0             0            0                 0          0     0   

   Castle  Chinese Restaurant  City  Clothing Store  Coffee Shop  Comic Shop  \
0       0                   0     0               0            0           0   
1       0                   0     0               0            0           0   
2       0                   0     0               0            0           0   
3       0                   0     0               0            0           0   
4       0                   0     0               0            0           0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  Cruise  \
0                           0                  0               0       0   
1                           0                  0               0       0   
2                           0                  0               0       0   
3                           0                  0               0       0   
4                           0                  0               0       0   

   Cupcake Shop  Dessert Shop  Diner  Donut Shop  Dry Cleaner  Event Space  \
0             0             0      0           0            0            0   
1             0             0      0           0            0            0   
2             0             0      0           0            0            0   
3             0             0      0           0            0            0   
4             0             0      0           0            0            0   

   Farm  Fast Food Restaurant  Financial or Legal Service  Flower Shop  Food  \
0     0                     0                           0            0     0   
1     0                     0                           0            0     0   
2     0                     0                           0            0     0   
3     0                     0                           0            0     0   
4     0                     0                           0            0     0   

   Food Court  Food Stand  Food Truck  Fountain  French Restaurant  \
0           0           0           0         0                  0   
1           0           0           0         0                  0   
2           0           0          

### Let's examine the new dataframe size

In [66]:
lazio_onehot.shape

(713, 133)

#### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [67]:
lazio_grouped = lazio_onehot.groupby('Town').mean().reset_index()
lazio_grouped

Town  Accessories Store  Airport Service  \
0                      Agosta            0.000000            0.000   
1              Albano Laziale            0.000000            0.000   
2                   Allumiere            0.000000            0.000   
3          Anguillara Sabazia            0.000000            0.000   
4            Anticoli Corrado            0.000000            0.000   
5                       Anzio            0.000000            0.000   
6            Arcinazzo Romano            0.000000            0.000   
7                       Ardea            0.000000            0.000   
8                     Ariccia            0.000000            0.000   
9                      Arsoli            0.000000            0.000   
10                     Artena            0.000000            0.000   
11         Campagnano di Roma            0.000000            0.000   
12           Canale Monterano            0.000000            0.000   
13                     Capena            0.000000            0.000   
14       Capranica Prenestina            0.000000            0.000   
15           Carpineto Romano            0.000000            0.000   
16                     Casape            0.000000            0.000   
17            Castel Gandolfo            0.000000            0.000   
18              Castel Madama            0.000000            0.000   
19   Castel San Pietro Romano            0.000000            0.000   
20       Castelnuovo di Porto            0.000000            0.000   
21                       Cave            0.000000            0.000   
22            Cerreto Laziale            0.000000            0.000   
23            Cervara di Roma            0.000000            0.000   
24                  Cerveteri            0.000000            0.000   
25                   Ciampino            0.000000            0.125   
26              Cineto Romano            0.000000            0.000   
27              Civitavecchia            0.000000            0.000   
28        Civitella San Paolo            0.000000            0.000   
29                 Colleferro            0.000000            0.000   
30                    Colonna            0.000000            0.000   
31               Fiano Romano            0.000000            0.000   
32                 Filacciano            0.000000            0.000   
33                  Fiumicino            0.000000            0.000   
34                Fonte Nuova            0.142857            0.000   
35                   Formello            0.000000            0.000   
36                   Frascati            0.000000            0.000   
37        Gallicano nel Lazio            0.000000            0.000   
38                  Gavignano            0.000000            0.000   
39                  Genazzano            0.000000            0.000   
40            Genzano di Roma            0.000000            0.000   
41                     Gerano            0.000000            0.000   
42                      Gorga            0.000000            0.000   
43              Grottaferrata            0.000000            0.000   
44                      Jenne            0.000000            0.000   
45                     Labico            0.000000            0.000   
46                  Ladispoli            0.000000            0.000   
47                    Lanuvio            0.000000            0.000   
48                    Lariano            0.000000            0.000   
49                    Licenza            0.000000            0.000   
50                    Mandela            0.000000            0.000   
51                   Manziana            0.000000            0.000   
52                Marano Equo            0.000000            0.000   
53                 Marcellina            0.000000            0.000   
54                     Marino            0.000000            0.000   
55             Mazzano Romano            0.000000            0.000   
56                    Mentana       

#### Let's confirm the new size

In [68]:
lazio_grouped.shape

(110, 133)

#### Let's print each neighborhood along with the top 5 most common venues

In [69]:
num_top_venues = 5

for hood in lazio_grouped['Town']:
    print("----"+hood+"----")
    temp = lazio_grouped[lazio_grouped['Town'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Agosta ----
         venue  freq
0  Snack Place   1.0
1     Mountain   0.0
2         Pier   0.0
3     Pharmacy   0.0
4    Pet Store   0.0


----Albano Laziale ----
                  venue  freq
0                  Café  0.50
1                 Hotel  0.25
2     Trattoria/Osteria  0.25
3     Accessories Store  0.00
4  Other Great Outdoors  0.00


----Allumiere ----
                venue  freq
0               Plaza   0.2
1   Trattoria/Osteria   0.2
2              Bakery   0.2
3          Restaurant   0.2
4  Italian Restaurant   0.2


----Anguillara Sabazia ----
                  venue  freq
0            Playground  0.25
1     Convenience Store  0.25
2         Grocery Store  0.25
3  Gym / Fitness Center  0.25
4  Other Great Outdoors  0.00


----Anticoli Corrado ----
               venue  freq
0              Hotel  0.25
1              Plaza  0.25
2                Pub  0.25
3     Scenic Lookout  0.25
4  Accessories Store  0.00


----Anzio ----
                venue  freq
0  Seafood Restaur

## Lets put that into a pandas dataframe

### First, let's write a function to sort the venues in descending order.

In [70]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

#### Now lets create a new dataframe to display the top 10 venues for each neighborhood.

In [71]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Town']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
Towns_venues_sorted = pd.DataFrame(columns=columns)
Towns_venues_sorted['Town'] = lazio_grouped['Town']

for ind in np.arange(lazio_grouped.shape[0]):
    Towns_venues_sorted.iloc[ind, 1:] = return_most_common_venues(lazio_grouped.iloc[ind, :], num_top_venues)

Towns_venues_sorted.head(20)

Town 1st Most Common Venue  \
0                     Agosta            Snack Place   
1             Albano Laziale                   Café   
2                  Allumiere                 Bakery   
3         Anguillara Sabazia          Grocery Store   
4           Anticoli Corrado                  Hotel   
5                      Anzio     Seafood Restaurant   
6           Arcinazzo Romano                    Bar   
7                      Ardea            Pizza Place   
8                    Ariccia     Italian Restaurant   
9                     Arsoli                   Café   
10                    Artena                   Park   
11        Campagnano di Roma            Pizza Place   
12          Canale Monterano                  Diner   
13                    Capena            Pizza Place   
14      Capranica Prenestina                   Café   
15          Carpineto Romano                  Plaza   
16                    Casape                   Café   
17           Castel Gandolfo     Italian Restaurant   
18             Castel Madama               Pharmacy   
19  Castel San Pietro Romano       Roman Restaurant   

         2nd Most Common Venue   3rd Most Common Venue 4th Most Common Venue  \
0                       Winery                    Food     French Restaurant   
1                        Hotel       Trattoria/Osteria           Flower Shop   
2            Trattoria/Osteria                   Plaza    Italian Restaurant   
3                   Playground       Convenience Store  Gym / Fitness Center   
4               Scenic Lookout                   Plaza                   Pub   
5                         Café      Italian Restaurant        Ice Cream Shop   
6           Italian Restaurant                  Winery     French Restaurant   
7               Cosmetics Shop         Bed & Breakfast                   Bar   
8                        Plaza        Roman Restaurant                  Food   
9           Italian Restaurant                  Winery                  Food   
10                Gourmet Shop                   Plaza                Winery   
11           Trattoria/Osteria                Pharmacy                 Hotel   
12                        City              Restaurant           Dry Cleaner   
13                        Café      Italian Restaurant                  Food   
14        Arts & Entertainment                  Winery                  Food   
15          Italian Restaurant                  Winery           Flower Shop   
16                      Winery  Furniture / Home Store           Dry Cleaner   
17                       Plaza                   Hotel                  City   
18  Construction & Landscaping                  Winery          Funeral Home   
19                  Public Art                  Winery           Flower Shop   

         5th Most Common Venue       6th Most Common Venue  \
0                     Fountain                  Food Truck   
1                     Fountain                  Food Truck   
2                   Restaurant  Financial or Legal Service   
3   Financial or Legal Service                  Food Truck   
4                  Flower Shop                  Food Truck   
5                        Diner                Dessert Shop   
6                     Fountain                  Food Truck   
7                  Event Space                 Dry Cleaner   
8                       Museum                  Restaurant   
9            French Restaurant                    Fountain   
10                  Food Truck                  Food Stand   
11                 Art Gallery          Alternative Healer   
12                 Event Space                        Farm   
13           French Restaurant                    Fountain   
14           French Restaurant                    Fountain   
15                    Fountain                  Food Truck   
16                 Event Space                        Farm   
17                        Lake                         Bar   
18        

## Clustering Neighborhoods

#### Run k-means clustering for the neighborhoods 

In [72]:
# set number of clusters
kclusters = 5

lazio_grouped_clustering = lazio_grouped.drop('Town', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(lazio_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([4, 1, 4, 4, 4, 4, 0, 4, 0, 1])

#### Let's create a new dataframe that includes the cluster as well as the top 10 venues for each town/neighborhood.

In [73]:
# add clustering labels
Towns_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

rome_merged = lazio_data

# merge lazio_grouped with lazio_data to add latitude/longitude for each town/neighborhood
rome_merged = rome_merged.join(Towns_venues_sorted.set_index('Town'), on='Town',how ='right')

rome_merged.head(102) # check the last columns!

Town Region Country   Latitude  Longitude  \
0                         Rome  Lazio   Italy  41.894802  12.485338   
2                      Agosta   Lazio   Italy  41.981624  13.032688   
3              Albano Laziale   Lazio   Italy  41.728889  12.658269   
4                   Allumiere   Lazio   Italy  42.156218  11.903832   
5          Anguillara Sabazia   Lazio   Italy  42.083709  12.282982   
6            Anticoli Corrado   Lazio   Italy  42.009524  12.989087   
7                       Anzio   Lazio   Italy  41.447101  12.628562   
8            Arcinazzo Romano   Lazio   Italy  41.879722  13.114392   
9                       Ardea   Lazio   Italy  41.608712  12.519382   
10                    Ariccia   Lazio   Italy  41.720709  12.671348   
11                     Arsoli   Lazio   Italy  42.040525  13.018387   
12                     Artena   Lazio   Italy  41.741915  12.912174   
16         Campagnano di Roma   Lazio   Italy  42.141078  12.383669   
17           Canale Monterano   Lazio   Italy  42.136043  12.103066   
19                     Capena   Lazio   Italy  42.140150  12.540201   
20       Capranica Prenestina   Lazio   Italy  41.862997  12.951802   
21           Carpineto Romano   Lazio   Italy  41.604413  13.084796   
22                     Casape   Lazio   Italy  41.907021  12.885786   
23            Castel Gandolfo   Lazio   Italy  41.742522  12.648877   
24              Castel Madama   Lazio   Italy  41.976936  12.869190   
25   Castel San Pietro Romano   Lazio   Italy  41.845720  12.894887   
26       Castelnuovo di Porto   Lazio   Italy  42.125399  12.500737   
27                       Cave   Lazio   Italy  41.817923  12.928367   
28            Cerreto Laziale   Lazio   Italy  41.944403  12.982805   
29            Cervara di Roma   Lazio   Italy  41.988224  13.067989   
30                  Cerveteri   Lazio   Italy  41.998360  12.098851   
31                   Ciampino   Lazio   Italy  41.800289  12.600471   
33              Cineto Romano   Lazio   Italy  42.049810  12.963073   
34              Civitavecchia   Lazio   Italy  42.093752  11.792246   
35        Civitella San Paolo   Lazio   Italy  42.198525  12.576475   
36                 Colleferro   Lazio   Italy  41.727033  13.004158   
37                    Colonna   Lazio   Italy  41.833718  12.753184   
38               Fiano Romano   Lazio   Italy  42.171913  12.592726   
39                 Filacciano   Lazio   Italy  42.254826  12.597675   
40                  Fiumicino   Lazio   Italy  41.767566  12.233947   
41                Fonte Nuova   Lazio   Italy  41.996254  12.623621   
42                   Formello   Lazio   Italy  42.082521  12.400273   
43                   Frascati   Lazio   Italy  41.808245  12.680368   
44        Gallicano nel Lazio   Lazio   Italy  41.872070  12.818534   
45                  Gavignano   Lazio   Italy  41.699118  13.051793   
46                  Genazzano   Lazio   Italy  41.829673  12.972246   
47            Genzano di Roma   Lazio   Italy  41.706989  12.691118   
48                     Gerano   Lazio   Italy  41.933119  12.993776   
49                      Gorga   Lazio   Italy  41.655017  13.109095   
50              Grottaferrata   Lazio   Italy  41.788616  12.666741   
52                      Jenne   Lazio   Italy  41.888823  13.169593   
53                     Labico   Lazio   Italy  41.789519  12.880888   
54                  Ladispoli   Lazio   Italy  41.953722  12.073465   
55                    Lanuvio   Lazio   Italy  41.674528  12.697243   
56                    Lariano   Lazio   Italy  41.725113  12.831276   
57                    Licenza   Lazio   Italy  42.073113  12.901468   
59                    Mandela   Lazio   Italy  42.030807  12.923323   
60                   Manziana   Lazio   Italy  42.130344  12.130271   
61                Marano Equo   Lazio   Italy  41.994024  13.015988   
62                 Marcellina   Lazio   Italy  42.023690  12.807045   
63                     Marino   Lazio   Italy  41.

#### Finally, let's visualize the resulting clusters

In [74]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(rome_merged['Latitude'], rome_merged['Longitude'], rome_merged['Town'], rome_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

## Examine Clusters

#### Examine each cluster and determine the discriminating venue categories that distinguish each cluster. Based on the defining categories, then assign a name to each cluster. 

#### Cluster 1

In [75]:
rome_merged.loc[rome_merged['Cluster Labels'] == 0, rome_merged.columns[[1] + list(range(5, rome_merged.shape[1]))]]

Region  Cluster Labels 1st Most Common Venue       2nd Most Common Venue  \
8    Lazio               0                   Bar          Italian Restaurant   
10   Lazio               0    Italian Restaurant                       Plaza   
39   Lazio               0    Italian Restaurant                      Winery   
52   Lazio               0              Mountain          Italian Restaurant   
94   Lazio               0    Italian Restaurant                      Winery   
99   Lazio               0    Italian Restaurant  Construction & Landscaping   
101  Lazio               0    Italian Restaurant                Dessert Shop   

    3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
8                  Winery        French Restaurant              Fountain   
10       Roman Restaurant                     Food                Museum   
39            Flower Shop        French Restaurant              Fountain   
52                   Food             Funeral Home     French Restaurant   
94            Flower Shop        French Restaurant              Fountain   
99         Hardware Store                   Winery           Flower Shop   
101    Alternative Healer  Health & Beauty Service                  Food   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8              Food Truck            Food Stand            Food Court   
10             Restaurant                 Diner     Trattoria/Osteria   
39             Food Truck            Food Stand            Food Court   
52               Fountain            Food Truck            Food Stand   
94             Food Truck            Food Stand            Food Court   
99               Fountain            Food Truck            Food Stand   
101     French Restaurant              Fountain            Food Truck   

    9th Most Common Venue      10th Most Common Venue  
8                    Food                 Flower Shop  
10                   Farm        Fast Food Restaurant  
39                   Food  Financial or Legal Service  
52             Food Court                      Winery  
94                   Food  Financial or Legal Service  
99             Food Court                        Food  
101            Food Stand                  Food Court

#### Cluster 2

In [76]:
rome_merged.loc[rome_merged['Cluster Labels'] == 1, rome_merged.columns[[1] + list(range(5, rome_merged.shape[1]))]]

Region  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
3    Lazio               1                  Café                 Hotel   
11   Lazio               1                  Café    Italian Restaurant   
19   Lazio               1           Pizza Place                  Café   
20   Lazio               1                  Café  Arts & Entertainment   
22   Lazio               1                  Café                Winery   
26   Lazio               1        Ice Cream Shop                  Café   
36   Lazio               1             Gastropub        Ice Cream Shop   
45   Lazio               1         Historic Site          Soccer Field   
47   Lazio               1                  Café    Italian Restaurant   
62   Lazio               1                  Café            Restaurant   
65   Lazio               1                   Bar                  Café   
67   Lazio               1              Pharmacy                Cruise   
76   Lazio               1    Italian Restaurant                  Café   
85   Lazio               1                  Food                  Café   
87   Lazio               1                Bakery              Pharmacy   
93   Lazio               1                  Café           IT Services   
113  Lazio               1                  Café  Other Great Outdoors   

      3rd Most Common Venue   4th Most Common Venue 5th Most Common Venue  \
3         Trattoria/Osteria             Flower Shop              Fountain   
11                   Winery                    Food     French Restaurant   
19       Italian Restaurant                    Food     French Restaurant   
20                   Winery                    Food     French Restaurant   
22   Furniture / Home Store             Dry Cleaner           Event Space   
26   Furniture / Home Store             Dry Cleaner           Event Space   
36                     Café              Food Court     French Restaurant   
45                     Café                  Winery                  Food   
47            Historic Site  Gluten-free Restaurant                Winery   
62              Flower Shop                Fountain            Food Truck   
65        Trattoria/Osteria      Chinese Restaurant                Winery   
67                     Café      Italian Restaurant                  Food   
76             Dessert Shop                    Lake                   Bar   
85    Outdoors & Recreation             Music Venue                Winery   
87                     Café             Flower Shop              Fountain   
93     Fast Food Restaurant  Furniture / Home Store           Dry Cleaner   
113             Supermarket                  Winery                  Food   

    6th Most Common Venue 7th Most Common Venue       8th Most Common Venue  \
3              Food Truck            Food Stand                  Food Court   
11               Fountain            Food Truck                  Food Stand   
19               Fountain            Food Truck                  Food Stand   
20               Fountain            Food Truck                  Food Stand   
22                   Farm  Fast Food Restaurant  Financial or Legal Service   
26                   Farm  Fast Food Restaurant  Financial or Legal Service   
36               Fountain            Food Truck                  Food Stand   
45               Fountain            Food Truck                  Food Stand   
47                   Food              Fountain                  Food Truck   
62             Food Stand            Food Court                        Food   
65               Fountain            Food Truck                  Food Stand   
67               Fountain            Food Truck                  Food Stand   
76            Pizza Place        Hardware Store               Historic Site   
85               Fountain            Food Truck                  Food Stand   
87             Food Truck            Food Stand                  Food Court   
93            Event 

#### Cluster 3

In [77]:
rome_merged.loc[rome_merged['Cluster Labels'] == 2, rome_merged.columns[[1] + list(range(5, rome_merged.shape[1]))]]

Region  Cluster Labels 1st Most Common Venue     2nd Most Common Venue  \
17   Lazio               2                 Diner                      City   
29   Lazio               2            Restaurant            Scenic Lookout   
48   Lazio               2            Restaurant                    Winery   
57   Lazio               2            Restaurant        Italian Restaurant   
66   Lazio               2            Restaurant  Mediterranean Restaurant   
91   Lazio               2            Restaurant                 Cafeteria   
100  Lazio               2            Restaurant                    Winery   
102  Lazio               2            Restaurant               Pizza Place   
103  Lazio               2            Restaurant        Seafood Restaurant   
107  Lazio               2            Restaurant                       Pub   

          3rd Most Common Venue 4th Most Common Venue  \
17                   Restaurant           Dry Cleaner   
29                   Food Truck           Flower Shop   
48                 Funeral Home            Donut Shop   
57                       Winery              Fountain   
66           Italian Restaurant           Flower Shop   
91                  Flower Shop              Fountain   
100                Funeral Home            Donut Shop   
102  Financial or Legal Service              Fountain   
103                  Donut Shop           Dry Cleaner   
107          Italian Restaurant                Winery   

          5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
17                  Event Space                  Farm  Fast Food Restaurant   
29                     Fountain            Food Stand            Food Court   
48                  Dry Cleaner           Event Space                  Farm   
57                   Food Truck            Food Stand            Food Court   
66                     Fountain            Food Truck            Food Stand   
91                   Food Truck            Food Stand            Food Court   
100                 Dry Cleaner           Event Space                  Farm   
102                  Food Truck            Food Stand            Food Court   
103                 Event Space                  Farm  Fast Food Restaurant   
107  Financial or Legal Service            Food Truck            Food Stand   

          8th Most Common Venue       9th Most Common Venue  \
17   Financial or Legal Service                Dessert Shop   
29                         Food                      Winery   
48         Fast Food Restaurant  Financial or Legal Service   
57                         Food                 Flower Shop   
66                   Food Court                        Food   
91                         Food                      Winery   
100        Fast Food Restaurant  Financial or Legal Service   
102                        Food                 Flower Shop   
103  Financial or Legal Service                Dessert Shop   
107                  Food Court                        Food   

         10th Most Common Venue  
17                  Flower Shop  
29                 Dessert Shop  
48                  Flower Shop  
57   Financial or Legal Service  
66                       Winery  
91                 Dessert Shop  
100                 Flower Shop  
102                      Winery  
103                 Flower Shop  
107                 Flower Shop

#### Cluster 4

In [78]:
rome_merged.loc[rome_merged['Cluster Labels'] == 3, rome_merged.columns[[1] + list(range(5, rome_merged.shape[1]))]]

Region  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
21  Lazio               3                 Plaza    Italian Restaurant   
30  Lazio               3                 Plaza            Restaurant   
33  Lazio               3            Smoke Shop                 Plaza   
75  Lazio               3                 Plaza                Winery   
90  Lazio               3                 Plaza                Winery   
95  Lazio               3                 Plaza           Pizza Place   
96  Lazio               3              Pharmacy                 Plaza   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
21                Winery           Flower Shop              Fountain   
30               Brewery                Museum           Flower Shop   
33           Flower Shop     French Restaurant              Fountain   
75          Funeral Home            Donut Shop           Dry Cleaner   
90          Funeral Home            Donut Shop           Dry Cleaner   
95                Winery           Flower Shop              Fountain   
96                Winery           Flower Shop              Fountain   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
21            Food Truck            Food Stand            Food Court   
30            Food Truck            Food Stand            Food Court   
33            Food Truck            Food Stand            Food Court   
75           Event Space                  Farm  Fast Food Restaurant   
90           Event Space                  Farm  Fast Food Restaurant   
95            Food Truck            Food Stand            Food Court   
96            Food Truck            Food Stand            Food Court   

         9th Most Common Venue 10th Most Common Venue  
21                        Food   Fast Food Restaurant  
30                        Food                 Winery  
33                        Food                 Winery  
75  Financial or Legal Service            Flower Shop  
90  Financial or Legal Service            Flower Shop  
95                        Food   Fast Food Restaurant  
96                        Food   Fast Food Restaurant

#### Cluster 5

In [79]:
rome_merged.loc[rome_merged['Cluster Labels'] == 4, rome_merged.columns[[1] + list(range(5, rome_merged.shape[1]))]]

Region  Cluster Labels   1st Most Common Venue  \
0    Lazio               4      Italian Restaurant   
2    Lazio               4             Snack Place   
4    Lazio               4                  Bakery   
5    Lazio               4           Grocery Store   
6    Lazio               4                   Hotel   
7    Lazio               4      Seafood Restaurant   
9    Lazio               4             Pizza Place   
12   Lazio               4                    Park   
16   Lazio               4             Pizza Place   
23   Lazio               4      Italian Restaurant   
24   Lazio               4                Pharmacy   
25   Lazio               4        Roman Restaurant   
27   Lazio               4             Pizza Place   
28   Lazio               4      Miscellaneous Shop   
31   Lazio               4                   Hotel   
34   Lazio               4      Italian Restaurant   
35   Lazio               4        Business Service   
37   Lazio               4                Pharmacy   
38   Lazio               4             Bridal Shop   
40   Lazio               4      Seafood Restaurant   
41   Lazio               4       Accessories Store   
42   Lazio               4             Pizza Place   
43   Lazio               4      Italian Restaurant   
44   Lazio               4                    Park   
46   Lazio               4             Flower Shop   
49   Lazio               4          Scenic Lookout   
50   Lazio               4      Italian Restaurant   
53   Lazio               4  Furniture / Home Store   
54   Lazio               4           Shopping Mall   
55   Lazio               4             Pizza Place   
56   Lazio               4          Ice Cream Shop   
59   Lazio               4             Pizza Place   
60   Lazio               4             Pizza Place   
61   Lazio               4          Breakfast Spot   
63   Lazio               4              Restaurant   
64   Lazio               4                  Bakery   
68   Lazio               4                   Diner   
69   Lazio               4             Pizza Place   
71   Lazio               4            Dessert Shop   
73   Lazio               4        Sculpture Garden   
74   Lazio               4                 Theater   
77   Lazio               4                   Hotel   
78   Lazio               4      Italian Restaurant   
79   Lazio               4                   Diner   
80   Lazio               4      Italian Restaurant   
81   Lazio               4                  Bakery   
82   Lazio               4              Playground   
83   Lazio               4            Funeral Home   
84   Lazio               4                     Bar   
86   Lazio               4             Event Space   
88   Lazio               4            Cupcake Shop   
89   Lazio               4   Outdoors & Recreation   
92   Lazio               4                   Plaza   
97   Lazio               4      Italian Restaurant   
98   Lazio               4             Pizza Place   
104  Lazio               4      Miscellaneous Shop   
105  Lazio               4      Italian Restaurant   
106  Lazio               4                    City   
109  Lazio               4           Historic Site   
110  Lazio               4                 Rafting   
111  Lazio               4      Italian Restaurant   
112  Lazio               4      Italian Restaurant   
114  Lazio               4      Italian Restaurant   
115  Lazio               4            Gourmet Shop   
117  Lazio               4             Pizza Place   
118  Lazio               4              Donut Shop   
119  Lazio               4             Pizza Place   
121  Lazio               4            Dessert Shop   
129  Lazio               4      Italian Restaurant   

          2nd Most Common Venue          3rd Most Common Venue  \
0                 Historic Site                          Plaza   
2                        Winery                           Food   
4             Trattoria/O